In [4]:
%load_ext autoreload
%autoreload 2

import numpy as np
from wordle_env import WordleEnv
import torch
import torch.nn as nn
import torch.nn.functional as F

In [14]:
from model import RNNAgent, get_allowed_letters

In [15]:
torch.autograd.set_detect_anomaly(True)

In [16]:
DEVICE = torch.device('cpu')

In [17]:
from wrappers import SequenceWrapper, ReshapeWrapper
from wrappers import nature_dqn_env

num_letters = 29
env = nature_dqn_env(nenvs=4)
from tokenizer import Tokenizer

tokenizer = Tokenizer()

game_voc_matrix = torch.FloatTensor(env.game_voc_matrix)
agent = RNNAgent(len(tokenizer.index2letter), len(tokenizer.index2guess_state), 32, 64, len(tokenizer.index2letter), output_len=5, sos_token=1, game_voc_matrix=game_voc_matrix)






[INFO/Process-6] child process calling self.run()
[INFO/Process-7] child process calling self.run()
[INFO/Process-8] child process calling self.run()
[INFO/Process-5] child process calling self.run()
[INFO/Process-6] child process calling self.run()
[INFO/Process-7] child process calling self.run()
[INFO/Process-8] child process calling self.run()
[INFO/Process-5] child process calling self.run()
[DEBUG/MainProcess] created semlock with handle 109
[DEBUG/MainProcess] created semlock with handle 111
[DEBUG/MainProcess] created semlock with handle 118


In [18]:
from runners import EnvRunner

runner = EnvRunner(env, agent, nsteps=6)

trajectory = runner.get_next()
print(f"Trajectory keys: {trajectory.keys()}")
print(f"Trajectory rewards: {trajectory['rewards']}")
print(f"Trajectory values: {trajectory['values']}")

[DEBUG/MainProcess] Queue._start_thread()
[DEBUG/MainProcess] doing self._thread.start()
[DEBUG/MainProcess] starting thread to feed data to pipe
[DEBUG/MainProcess] ... done self._thread.start()


Trajectory keys: dict_keys(['actions', 'log_probs', 'values', 'observations', 'rewards', 'dones'])
Trajectory rewards: [array([0. , 0. , 0. , 0.2]), array([0. , 0.2, 0.2, 0. ]), array([ 0. ,  0.2, -0.2, -0.2]), array([-0.2, -0.2,  0. ,  0.2]), array([ 0. , -0.2, -0.2,  0. ]), array([ 0. ,  0. ,  0. , -0.4])]
Trajectory values: [tensor([0.1021, 0.1021, 0.1021, 0.1021], grad_fn=<ViewBackward>), tensor([0.1021, 0.1021, 0.1021, 0.1021], grad_fn=<ViewBackward>), tensor([0.1020, 0.1020, 0.1020, 0.1020], grad_fn=<ViewBackward>), tensor([0.1018, 0.1018, 0.1018, 0.1018], grad_fn=<ViewBackward>), tensor([0.1011, 0.1010, 0.1012, 0.1011], grad_fn=<ViewBackward>), tensor([0.0978, 0.0983, 0.0988, 0.0985], grad_fn=<ViewBackward>)]


In [19]:
nenvs = 4

# Sanity checks
# assert 'logits' in trajectory, "Not found: policy didn't provide logits"
assert 'log_probs' in trajectory, "Not found: policy didn't provide log_probs of selected actions"
assert 'values' in trajectory, "Not found: policy didn't provide critic estimations"
# assert trajectory['logits'][0].shape == (nenvs, n_actions), "logits wrong shape"
assert trajectory['log_probs'][0].shape == (nenvs,), "log_probs wrong shape"
assert trajectory['values'][0].shape == (nenvs,), "values wrong shape"

for key in trajectory.keys():
    assert len(trajectory[key]) == 6, \
    f"something went wrong: 6 steps should have been done, got trajectory of length {len(trajectory[key])} for '{key}'"


In [20]:
trajectory['values']

[tensor([0.1021, 0.1021, 0.1021, 0.1021], grad_fn=<ViewBackward>),
 tensor([0.1021, 0.1021, 0.1021, 0.1021], grad_fn=<ViewBackward>),
 tensor([0.1020, 0.1020, 0.1020, 0.1020], grad_fn=<ViewBackward>),
 tensor([0.1018, 0.1018, 0.1018, 0.1018], grad_fn=<ViewBackward>),
 tensor([0.1011, 0.1010, 0.1012, 0.1011], grad_fn=<ViewBackward>),
 tensor([0.0978, 0.0983, 0.0988, 0.0985], grad_fn=<ViewBackward>)]

In [21]:
trajectory['values'][0].shape

torch.Size([4])

In [29]:
from transforms import ComputeValueTargets, MergeTimeBatch
from a2c import A2C

In [ ]:
runner = EnvRunner(env, agent, nsteps=4, transforms=[ComputeValueTargets(agent, gamma=0.9),
                                                      MergeTimeBatch()])
trajectory = runner.get_next()

In [25]:
env.close()

[INFO/Process-6] process shutting down
[INFO/Process-8] process shutting down
[INFO/Process-6] process shutting down
[INFO/Process-8] process shutting down
[INFO/Process-5] process shutting down
[DEBUG/Process-8] running all "atexit" finalizers with priority >= 0
[DEBUG/Process-6] running all "atexit" finalizers with priority >= 0
[INFO/Process-5] process shutting down
[DEBUG/Process-8] running all "atexit" finalizers with priority >= 0
[DEBUG/Process-6] running all "atexit" finalizers with priority >= 0
[DEBUG/Process-8] running the remaining "atexit" finalizers
[DEBUG/Process-6] running the remaining "atexit" finalizers
[DEBUG/Process-5] running all "atexit" finalizers with priority >= 0
[DEBUG/Process-8] running the remaining "atexit" finalizers
[INFO/Process-7] process shutting down
[DEBUG/Process-6] running the remaining "atexit" finalizers
[DEBUG/Process-5] running all "atexit" finalizers with priority >= 0
[INFO/Process-7] process shutting down
[DEBUG/Process-5] running the rema

In [26]:
from wordle_env import WordleEnv
from wrappers import SequenceWrapper, ReshapeWrapper, TensorboardSummaries
from wrappers import nature_dqn_env
from env_batch import SingleEnvBatch

env = WordleEnv()
env = SequenceWrapper(env, sos_token=1)
env = SingleEnvBatch(env)
env = TensorboardSummaries(env, prefix='wordle')

# env = nature_dqn_env(nenvs=4)

[DEBUG/MainProcess] created semlock with handle 126
[DEBUG/MainProcess] created semlock with handle 127
[DEBUG/MainProcess] created semlock with handle 128


In [27]:
env.step(np.array([[5, 5, 5, 5, 5]]))[0].shape

(1, 2, 36)

In [28]:
from torch.optim import RMSprop

nenvs = 4
nsteps = 32
total_steps = 10 ** 6

# env = nature_dqn_env("SpaceInvadersNoFrameskip-v4", nenvs=nenvs)
# n_actions = env.action_space.spaces[0].n
obs = env.reset()

# model = Model(obs.shape[1:], n_actions).to(DEVICE)
policy = RNNAgent(
    len(tokenizer.index2letter), 
    len(tokenizer.index2guess_state), 
    32, 128, 
    len(tokenizer.index2letter), 
    output_len=5, 
    sos_token=1, 
    game_voc_matrix=game_voc_matrix
)

runner = EnvRunner(env, policy, nsteps=nsteps, transforms=[ComputeValueTargets(policy),
                                                      MergeTimeBatch()])
optimizer = RMSprop(policy.parameters(), 7e-4)
a2c = A2C(policy, optimizer, max_grad_norm=1.0)

[Level 5/MainProcess] finalizer calling <function close_fds at 0x7f837a9794c0> with args [115, 121] and kwargs {}
[Level 5/MainProcess] finalizer calling <function close_fds at 0x7f837a9794c0> with args [114, 119] and kwargs {}
[Level 5/MainProcess] finalizer calling <function close_fds at 0x7f837a9794c0> with args [112, 117] and kwargs {}
[Level 5/MainProcess] finalizer calling <function close_fds at 0x7f837a9794c0> with args [113, 116] and kwargs {}


In [ ]:
from tqdm import trange

obs = env.reset()
for step in trange(0, total_steps + 1, nenvs * nsteps):
    if step % 1000 == 0 and step > 0:
        torch.save(a2c.policy.state_dict(), f"model_weights/step_{step}")

    a2c.train(runner)

  0%|                                                                                                                                            | 0/7813 [00:00<?, ?it/s][DEBUG/MainProcess] Queue._start_thread()
[DEBUG/MainProcess] doing self._thread.start()
[DEBUG/MainProcess] starting thread to feed data to pipe
[DEBUG/MainProcess] ... done self._thread.start()
[DEBUG/MainProcess] created semlock with handle 521
[DEBUG/MainProcess] created semlock with handle 522
[DEBUG/MainProcess] created semlock with handle 523
[DEBUG/MainProcess] Queue._start_thread()
[DEBUG/MainProcess] doing self._thread.start()
[DEBUG/MainProcess] starting thread to feed data to pipe
[DEBUG/MainProcess] ... done self._thread.start()
[DEBUG/MainProcess] created semlock with handle 529
[DEBUG/MainProcess] created semlock with handle 530
[DEBUG/MainProcess] created semlock with handle 531
[DEBUG/MainProcess] Queue._start_thread()
[DEBUG/MainProcess] doing self._thread.start()
[DEBUG/MainProcess] starting thread t

[tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0015], grad_fn=<ViewBackward>), tensor([0.0016], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0012], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0010], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0014], grad_fn=<ViewBackward>), tensor([0.0014], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0013], grad_fn=<ViewBackward>), tensor([0.0015], grad_fn=<ViewBackward>), tensor([0.0022], grad_fn=<ViewBac

  0%|                                                                                                                                 | 1/7813 [00:06<14:10:52,  6.54s/it]

[tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5672], grad_fn=<ViewBackward>), tensor([-0.5657], grad_fn=<ViewBackward>), tensor([-0.5354], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5670], grad_fn=<ViewBackward>), tensor([-0.5657], grad_fn=<ViewBackward>), tensor([-0.5398], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5659], grad_fn=<ViewBackward>), tensor([-0.5373], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0.5657], grad_fn=<ViewBackward>), tensor([-0.5343], grad_fn=<ViewBackward>), tensor([-0.5671], grad_fn=<ViewBackward>), tensor([-0

  0%|                                                                                                                                 | 2/7813 [00:13<14:09:58,  6.53s/it]

...

 45%|████████████████████████████████████████████████████████▌                                                                    | 3533/7813 [6:23:15<7:44:31,  6.51s/it]

[tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0021], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0020], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0022], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBackward>), tensor([0.0021], grad_fn=<ViewBackward>), tensor([0.0032], grad_fn=<ViewBac

 45%|████████████████████████████████████████████████████████▌                                                                    | 3534/7813 [6:23:21<7:43:12,  6.50s/it]

[tensor([8.4974e-06], grad_fn=<ViewBackward>), tensor([-2.5325e-05], grad_fn=<ViewBackward>), tensor([-0.0015], grad_fn=<ViewBackward>), tensor([1.1738e-05], grad_fn=<ViewBackward>), tensor([1.1668e-05], grad_fn=<ViewBackward>), tensor([1.1344e-05], grad_fn=<ViewBackward>), tensor([7.8045e-06], grad_fn=<ViewBackward>), tensor([-2.8692e-05], grad_fn=<ViewBackward>), tensor([-0.0010], grad_fn=<ViewBackward>), tensor([1.1738e-05], grad_fn=<ViewBackward>), tensor([1.1701e-05], grad_fn=<ViewBackward>), tensor([1.1321e-05], grad_fn=<ViewBackward>), tensor([8.9146e-06], grad_fn=<ViewBackward>), tensor([-1.9092e-05], grad_fn=<ViewBackward>), tensor([-0.0007], grad_fn=<ViewBackward>), tensor([1.1738e-05], grad_fn=<ViewBackward>), tensor([1.1671e-05], grad_fn=<ViewBackward>), tensor([1.1213e-05], grad_fn=<ViewBackward>), tensor([8.3782e-06], grad_fn=<ViewBackward>), tensor([-3.4239e-05], grad_fn=<ViewBackward>), tensor([-0.0008], grad_fn=<ViewBackward>), tensor([1.1738e-05], grad_fn=<ViewBackwar

 45%|████████████████████████████████████████████████████████▌                                                                    | 3535/7813 [6:23:28<7:44:38,  6.52s/it]

In [ ]:
torch.save(policy.state_dict(), 'model_weights/better_policy.pth')

In [ ]:
obs = env.reset()

In [ ]:
# test get_allowed_letters
from wrappers import SequenceWrapper, ReshapeWrapper
from wrappers import nature_dqn_env

num_letters = 29

env = WordleEnv()
env = SequenceWrapper(env, sos_token=1)
env = ReshapeWrapper(env)

In [ ]:
def transform2word(word_vector):
    letter_list = list(map(lambda x: env.tokenizer.index2letter[x], word_vector))
    return ''.join(letter_list)

In [ ]:
policy = RNNAgent(
    len(tokenizer.index2letter), 
    len(tokenizer.index2guess_state), 
    64, 32, 
    len(tokenizer.index2letter), 
    output_len=5, 
    sos_token=1, 
    game_voc_matrix=game_voc_matrix
)

In [ ]:
tokenizer.guess_state2index

In [ ]:
obs = env.reset()

env_word = env.word
print(f"Real word: {transform2word(env.word)}")

for _ in range(6):
    action = a2c.policy.act(obs)['actions'].squeeze()
    obs, rew, done, info = env.step(action)
    print((obs[:, 1, :] == 3).sum())
    print(obs)
    print(f"guess: {transform2word(action)}, reward: {rew[0]}")

In [ ]:
obs

In [ ]:
obs = env.reset()
env_word = env.word
print(f"Real word: {transform2word(env.word)}")

In [ ]:
action = np.array([6, 6, v, 8, 8])
obs, rew, done, info = env.step(action)
print(f"guess: {transform2word(action)}, reward: {rew[0]}")

In [ ]:
obs

In [ ]:
action

In [ ]:
action == env_word

In [ ]:
obs = env.reset()
done = False

print(f"True word: {transform2word(env.word)}")

print("guesses:")
print("--------")

while not done:
    action = agent.act(obs)['actions'].squeeze()
    obs, rew, done, info = env.step(action)
    print(f"{transform2word(action)} (reward = {rew})")

In [ ]:
GAME_VOCABULARY